# Web Mercator Tiles

Tyler Erickson  
2024-09-09

The internet is full of interactive tiled *slippy* web maps. These maps
load tiles as needed in response to the user zooming and panning around,
which allows users to explore extremely large datasets with minimal
lagtime. This style of web map was first popularized by [Google Maps in
2005](https://en.wikipedia.org/wiki/Google_Maps#2005%E2%80%932010), and
since then the approach has been adopted by other mapping libraries,
such as [Leaflet.js](https://leafletjs.com/),
[OpenLayers](https://openlayers.org/),
[Mapbox](https://docs.mapbox.com/api/maps/static-tiles/) and many
others. These interactive maps utilize an [XYZ tiling
scheme](https://en.wikipedia.org/wiki/Tiled_web_map#Defining_a_tiled_web_map),
where Z represents the zoom level and X and Y are denote the tile
indices.

<figure id="fig-xyz-tiles">
<img
src="https://upload.wikimedia.org/wikipedia/commons/thumb/d/d6/XYZ_Tiles.png/1024px-XYZ_Tiles.png" />
<figcaption>Figure 1: Overview of web mercator tiles zoom levels 0
through 5 with an example tile for each zoom level. Source: <a
href="https://commons.wikimedia.org/wiki/File:XYZ_Tiles.png">File:XYZ
Tiles.png</a>. License <a
href="https://creativecommons.org/publicdomain/zero/1.0/deed.en">CC0</a>.
If you prefer an interactive 2-D map, check out MapTiler’s <a
href="https://docs.maptiler.com/google-maps-coordinates-tile-bounds-projection">Tiles
à la Google Maps</a>.</figcaption>
</figure>

These tiles use a [Web (pseudo)
Mercator](https://en.wikipedia.org/wiki/Web_Mercator_projection)
projection ([EPSG:3857](https://spatialreference.org/ref/epsg/3857/)),
which is defined using a strange mix of ellipsoidal and spherical
properties. If you care about positional accuracy, [use this projection
at your own
risk](https://web.archive.org/web/20170329065451/https://earth-info.nga.mil/GandG/wgs84/web_mercator/index.html).
Also the projection strongly distorts areas. For example, compare how
Greenland and Africa appear to be similar in size (2.2 million
$\text{km}^2$ and 30.4 million $\text{km}^2$, respectively).

But if you are creating an interactive map for the web, the projection
can be very useful.

# Mathematical Description

The Web Mercator projection is
[defined](https://en.wikipedia.org/wiki/Web_Mercator_projection#Formulas)
by the following formulas. The tile’s $x$-index is a function of
longitude ($\lambda$) and zoom level ($z$):
<span id="eq-web-mercator-x">$$
x = {\frac {1}{2\pi }}\cdot 2^z\left(\pi +\lambda \right)
 \qquad(1)$$</span> and the tile’s $y$-index is a function of latitude
($\varphi$): <span id="eq-web-mercator-y">$$
y =  \frac{1}{2\pi } \cdot 2^z\left(\pi -\ln \left[\tan \left({\frac {\pi }{4}} + \frac{\varphi }{2}\right)\right]\right)
 \qquad(2)$$</span>

Rearranging
<a href="#eq-web-mercator-x" class="quarto-xref">Equation 1</a> to solve
for longitude ($\lambda$) yields: <span id="eq-longitude-from-xyz">$$
\lambda = \frac{2\pi \cdot x}{2^z} - \pi
 \qquad(3)$$</span>

and rearranging
<a href="#eq-web-mercator-y" class="quarto-xref">Equation 2</a> to solve
for latitude ($\varphi$) yields: <span id="eq-latitude-from-xyz">$$
\varphi = 2 \cdot \arctan(e^{\pi - \frac{2\pi \cdot y}{2^z}}) - {\frac {\pi }{2}}
 \qquad(4)$$</span>

# Python Implementation

In Python those equations can be written as:

In [1]:
import numpy as np
import numpy.typing as npt

def xyz_to_lonlat(
    x: npt.NDArray[np.floating], # horizontal index
    y: npt.NDArray[np.floating], # vertical index
    z: int, # zoom level
):
    lon = 2 * np.pi * x / 2**z - np.pi
    lat = 2 * np.arctan(np.exp(np.pi - (2 * np.pi * y / 2**z))) - np.pi / 2
    return (lon * 180 / np.pi, lat * 180 / np.pi)

To understand how tiles differ between levels and across the Earth, we
create a GeoDataFrame object containing the tile information.

In [2]:
import geopandas as gpd
import shapely

zoom_levels = [0, 1, 2, 3, 4]

# for layer in layer_config_list:
tile_data_list = []
for zoom in zoom_levels:
    tilerange = range(2**zoom + 1)

    # Create arrays of cell vertices.
    x_vertices = np.array(tilerange)
    y_vertices = np.array(tilerange)

    # Convert vertices to lon/lat coordinates.
    lons, lats = xyz_to_lonlat(x_vertices, y_vertices, zoom)

    for ix in tilerange[:-1]:
        for iy in tilerange[:-1]:
            poly_coords = [
                (lons[ix], lats[iy]),
                (lons[ix + 1], lats[iy]),
                (lons[ix + 1], lats[iy + 1]),
                (lons[ix], lats[iy + 1])
            ]
            # print('poly_coords', poly_coords)

            tile_data = {
                'zoom': zoom,
                'x_index': ix,
                'y_index': iy,
                'geometry': shapely.Polygon(poly_coords),
            }
            tile_data_list.append(tile_data)

gdf = gpd.GeoDataFrame(
    data=tile_data_list,
    crs="EPSG:4326"
)


Based on code described in [this earlier
post](../on-areas-on-earth/index.ipynb), we can calculate the area
covered by each tile.

In [3]:
import math

def patch_area_single_rectangle(
    R: float, # Authalic radius, in meters
    lon1: float, # Minimum longitude, in degrees
    lat1: float, # Minimum latitude, in degrees
    lon2: float, # Maximum longitude, in degrees
    lat2: float, # Maximum latitude, in degrees
) -> float:
    # Convert from degrees to radians
    lon1_rad = lon1 * (np.pi / 180)
    lon2_rad = lon2 * (np.pi / 180)
    lat1_rad = lat1 * (np.pi / 180)
    lat2_rad = lat2 * (np.pi / 180)
    
    h = R * (math.sin(lat2_rad) - math.sin(lat1_rad))
    area_patch = R * h  * (lon2_rad - lon1_rad)
    return area_patch

gdf['area_km2'] = gdf.apply(
    lambda row:patch_area_single_rectangle(
        6371007.180918,  # Authalic radius, in meters
        *row['geometry'].bounds,  # tuple of (minx, miny, maxx, maxy)
    ) * 1e-6,
    axis=1
)

Let’s see a summary of this tile dataset.

In [4]:
gdf

341 rows × 5 columns

Among other things, the data table shows that tile areas vary by y_index
and zoom level. But it is difficult to grasp how these values change
around the Earth from a table.

# Tile Visualization

This section creates visualizations of Web Mercator tiles for various
zoom levels. We start by formatting the tile data so that can be used by
[PyDeck](https://deckgl.readthedocs.io/).

In [5]:
tile_colors = [
    [0, 0, 0],
    [255, 255, 255],
]

def add_pydeck_colums(gdf):
    """Add columns for PyDeck visualization"""
    
    # Convert geodataframe geometries into a PyDeck compatible format
    gdf['pydeck_polygon'] = [
        [
            vertex + (200000, )  # Add a third dimension
            for vertex in list(geom.exterior.coords)
        ]
        for geom in gdf['geometry'].geometry
    ]
    gdf['pydeck_centroid'] = [
        list(geom.centroid.coords[0]) + [800000] # Add a third dimension
        for geom in gdf['geometry'].geometry
    ]
    gdf['centroid_label'] = '(' + gdf['x_index'].astype(str) + ',' + gdf['y_index'].astype(str) + ')'
    gdf['bounds'] = [
        [f'{x:.2f}' for x in geom.bounds]
        for geom in gdf['geometry'].geometry
    ]

    gdf['fill_color'] = gdf.apply(
        lambda row: tile_colors[(row['x_index'] + row['y_index']) % 2],
        axis=1
    )

    gdf['area_desc'] = gdf.apply(
        lambda row: f"{row['area_km2']:.2e}", 
        axis=1
    )

    return gdf

gdf = add_pydeck_colums(gdf)

We then create a function that can generate PyDeck objects for a
specified zoom level.

In [6]:
import pydeck as pdk
from pydeck.types import String
import pandas as pd

def get_globe_view():
    """Return a pyDeck view for the globe."""
    view = pdk.View(
        type="_GlobeView",
        controller=True,
        width='100%',
    )
    return view

def get_initial_view_state():
    """Specify the initial pyDeck view state."""
    initial_view_state = pdk.ViewState(
        latitude=45,
        longitude=-45,
        zoom=0,
        min_zoom=0,
    )
    return initial_view_state

def get_basemap_layer():
    """Get a pyDeck layer based on Natural Earth country boundaries."""
    basemap_layer = pdk.Layer(
        "GeoJsonLayer",
        id="base-map",
        data="https://d2ad6b4ur7yvpq.cloudfront.net/naturalearth-3.3.0/ne_50m_admin_0_scale_rank.geojson",
        stroked=False,
        filled=True,
        extruded=False,
        get_fill_color=[200, 200, 200],
        get_line_color=[255, 255, 255],
        opacity=0.5,
    )
    return basemap_layer

def get_tiles(zoom):
    """Create a pyDeck polygon and text layers for tiles of a specified zoom level."""
    poly_layer = pdk.Layer(
        "SolidPolygonLayer",
        gdf[gdf['zoom']==zoom],
        opacity=0.25,
        visible=True,
        get_polygon="pydeck_polygon",
        get_fill_color="fill_color",
        extruded=True,
    )

    text_layer = pdk.Layer(
        "TextLayer",
        gdf[gdf['zoom']==zoom],
        get_position="pydeck_centroid",
        get_text="centroid_label",
        get_size=12,
        # get_color=[127, 255, 255],
        get_color=[255, 255, 0],
        get_angle=0,
        get_text_anchor=String("middle"),
        get_alignment_baseline=String("center"),
        pickable=True,
        extruded=True,
    )
    return [poly_layer, text_layer]


def create_globe_with_xyz_tiles(zoom):
    
    # gdf = layer_config['gdf']
    deck = pdk.Deck(
        views=[get_globe_view()],
        initial_view_state=get_initial_view_state(),
        layers=[
            get_basemap_layer(),
            get_tiles(zoom),
        ],
        map_provider=None,
        tooltip={
            "html": (
                "<table>"
                "<tr><th>Zoom:</th><td>{zoom}</td></tr>"
                "<tr><th>X, Y:</th><td>{x_index}, {y_index}</td></tr>"
                "<tr><th>Area, km<sup>2</sup>:</th><td>{area_desc}</td></tr>"
                "<tr><th>Longitude:</th><td>{bounds.0}&deg; to {bounds.2}&deg;</td></tr>"
                "<tr><th>Latitude:</th><td>{bounds.1}&deg; to {bounds.3}&deg;</td></tr>"
                "</table>"
            ),
            "style": {
                "text-align": "right",
            }
        },
        # Note: set to True for the globe to be opaque
        parameters={"cull": True},
    )
    return deck

The following figures show how the Web Mercator tiles are distributed on
the globe for zoom levels 1 through 4. Viewing Web Mercator tiles this
way clearly shows that the tiles do not reach the poles, regardless of
the zoom level. Rather the tiles end at latitudes $85.051\degree$ N and
$85.051\degree$ S[1].

## Tiles - Zoom Level 1

For zoom level 1, the `x` and `y` tile indices range from 0 to 1[2].
There are a total of 4 tiles[3].

[1] $\varphi_{max} = 2 \cdot \arctan(e^{\pi}) - {\frac {\pi }{2}} = 85.051\degree$
(which is
<a href="#eq-latitude-from-xyz" class="quarto-xref">Equation 4</a>
simplified with $y=0$)

[2] $z=1; \ \ 2^z - 1 = 1$

[3] $z=1; \ \ 4^z = 4$ tiles

In [7]:
create_globe_with_xyz_tiles(1)

<iframe
 width="100%"
 height=500
 frameborder="0"
 srcdoc="<!DOCTYPE html>
<html>
 <head>
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 <title>pydeck</title>
 <script src="https://api.tiles.mapbox.com/mapbox-gl-js/v1.13.0/mapbox-gl.js"></script>
 <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css" />
 <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css" />
 <script src='https://cdn.jsdelivr.net/npm/@deck.gl/jupyter-widget@~8.8.*/dist/index.js'></script>
 <style>
 body {
 margin: 0;
 padding: 0;
 overflow: hidden;
}

#deck-container {
 width: 100vw;
 height: 100vh;
}

#deck-container canvas {
 z-index: 1;
 background: none;
}
 </style>
 </head>
 <body>
 <div id="deck-container">
 </div>
 </body>
 <script>
 const container = document.getElementById('deck-container');
 const jsonInput = {
 "initialViewState": {
 "latitude": 45,
 "longitude": -45,
 "minZoom": 0,
 "zoom": 0
 },
 "layers": [
 {
 "@@type": "GeoJsonLayer",
 "data": "https://d2ad6b4ur7yvpq.cloudfront.net/naturalearth-3.3.0/ne_50m_admin_0_scale_rank.geojson",
 "extruded": false,
 "filled": true,
 "getFillColor": [
 200,
 200,
 200
 ],
 "getLineColor": [
 255,
 255,
 255
 ],
 "id": "base-map",
 "opacity": 0.5,
 "stroked": false
 },
 [
 {
 "@@type": "SolidPolygonLayer",
 "data": [
 {
 "area_desc": "1.27e+08",
 "area_km2": 127041033.99095242,
 "bounds": [
 "-180.00",
 "0.00",
 "0.00",
 "85.05"
 ],
 "centroid_label": "(0,0)",
 "fill_color": [
 0,
 0,
 0
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 85.05112877980659
 ],
 [
 0.0,
 85.05112877980659
 ],
 [
 0.0,
 0.0
 ],
 [
 -180.0,
 0.0
 ],
 [
 -180.0,
 85.05112877980659
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -90.0,
 42.5255643899033,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 85.05112877980659,
 200000
 ],
 [
 0.0,
 85.05112877980659,
 200000
 ],
 [
 0.0,
 0.0,
 200000
 ],
 [
 -180.0,
 0.0,
 200000
 ],
 [
 -180.0,
 85.05112877980659,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 0,
 "zoom": 1
 },
 {
 "area_desc": "1.27e+08",
 "area_km2": 127041033.99095242,
 "bounds": [
 "-180.00",
 "-85.05",
 "0.00",
 "0.00"
 ],
 "centroid_label": "(0,1)",
 "fill_color": [
 255,
 255,
 255
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 0.0
 ],
 [
 0.0,
 0.0
 ],
 [
 0.0,
 -85.05112877980659
 ],
 [
 -180.0,
 -85.05112877980659
 ],
 [
 -180.0,
 0.0
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -90.0,
 -42.5255643899033,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 0.0,
 200000
 ],
 [
 0.0,
 0.0,
 200000
 ],
 [
 0.0,
 -85.05112877980659,
 200000
 ],
 [
 -180.0,
 -85.05112877980659,
 200000
 ],
 [
 -180.0,
 0.0,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 1,
 "zoom": 1
 },
 {
 "area_desc": "1.27e+08",
 "area_km2": 127041033.99095242,
 "bounds": [
 "0.00",
 "0.00",
 "180.00",
 "85.05"
 ],
 "centroid_label": "(1,0)",
 "fill_color": [
 255,
 255,
 255
 ],
 "geometry": {
 "coordinates": [
 [
 [
 0.0,
 85.05112877980659
 ],
 [
 180.0,
 85.05112877980659
 ],
 [
 180.0,
 0.0
 ],
 [
 0.0,
 0.0
 ],
 [
 0.0,
 85.05112877980659
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 90.0,
 42.5255643899033,
 800000
 ],
 "pydeck_polygon": [
 [
 0.0,
 85.05112877980659,
 200000
 ],
 [
 180.0,
 85.05112877980659,
 200000
 ],
 [
 180.0,
 0.0,
 200000
 ],
 [
 0.0,
 0.0,
 200000
 ],
 [
 0.0,
 85.05112877980659,
 200000
 ]
 ],
 "x_index": 1,
 "y_index": 0,
 "zoom": 1
 },
 {
 "area_desc": "1.27e+08",
 "area_km2": 127041033.99095242,
 "bounds": [
 "0.00",
 "-85.05",
 "180.00",
 "0.00"
 ],
 "centroid_label": "(1,1)",
 "fill_color": [
 0,
 0,
 0
 ],
 "geometry": {
 "coordinates": [
 [
 [
 0.0,
 0.0
 ],
 [
 180.0,
 0.0
 ],
 [
 180.0,
 -85.05112877980659
 ],
 [
 0.0,
 -85.05112877980659
 ],
 [
 0.0,
 0.0
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 90.0,
 -42.5255643899033,
 800000
 ],
 "pydeck_polygon": [
 [
 0.0,
 0.0,
 200000
 ],
 [
 180.0,
 0.0,
 200000
 ],
 [
 180.0,
 -85.05112877980

## Tiles - Zoom Level 2

For zoom level 2, the `x` and `y` tile indices range from 0 to 3[1].
There are a total of 16 tiles[2].

[1] $z=2; \ \ 2^z - 1 = 3$

[2] $z=2; \ \ 4^z = 16$ tiles

In [8]:
create_globe_with_xyz_tiles(2)

<iframe
 width="100%"
 height=500
 frameborder="0"
 srcdoc="<!DOCTYPE html>
<html>
 <head>
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 <title>pydeck</title>
 <script src="https://api.tiles.mapbox.com/mapbox-gl-js/v1.13.0/mapbox-gl.js"></script>
 <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css" />
 <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css" />
 <script src='https://cdn.jsdelivr.net/npm/@deck.gl/jupyter-widget@~8.8.*/dist/index.js'></script>
 <style>
 body {
 margin: 0;
 padding: 0;
 overflow: hidden;
}

#deck-container {
 width: 100vw;
 height: 100vh;
}

#deck-container canvas {
 z-index: 1;
 background: none;
}
 </style>
 </head>
 <body>
 <div id="deck-container">
 </div>
 </body>
 <script>
 const container = document.getElementById('deck-container');
 const jsonInput = {
 "initialViewState": {
 "latitude": 45,
 "longitude": -45,
 "minZoom": 0,
 "zoom": 0
 },
 "layers": [
 {
 "@@type": "GeoJsonLayer",
 "data": "https://d2ad6b4ur7yvpq.cloudfront.net/naturalearth-3.3.0/ne_50m_admin_0_scale_rank.geojson",
 "extruded": false,
 "filled": true,
 "getFillColor": [
 200,
 200,
 200
 ],
 "getLineColor": [
 255,
 255,
 255
 ],
 "id": "base-map",
 "opacity": 0.5,
 "stroked": false
 },
 [
 {
 "@@type": "SolidPolygonLayer",
 "data": [
 {
 "area_desc": "5.04e+06",
 "area_km2": 5044532.457006394,
 "bounds": [
 "-180.00",
 "66.51",
 "-90.00",
 "85.05"
 ],
 "centroid_label": "(0,0)",
 "fill_color": [
 0,
 0,
 0
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 85.05112877980659
 ],
 [
 -90.0,
 85.05112877980659
 ],
 [
 -90.0,
 66.51326044311185
 ],
 [
 -180.0,
 66.51326044311185
 ],
 [
 -180.0,
 85.05112877980659
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -135.0,
 75.78219461145922,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 85.05112877980659,
 200000
 ],
 [
 -90.0,
 85.05112877980659,
 200000
 ],
 [
 -90.0,
 66.51326044311185,
 200000
 ],
 [
 -180.0,
 66.51326044311185,
 200000
 ],
 [
 -180.0,
 85.05112877980659,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 0,
 "zoom": 2
 },
 {
 "area_desc": "5.85e+07",
 "area_km2": 58475984.53846981,
 "bounds": [
 "-180.00",
 "0.00",
 "-90.00",
 "66.51"
 ],
 "centroid_label": "(0,1)",
 "fill_color": [
 255,
 255,
 255
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 66.51326044311185
 ],
 [
 -90.0,
 66.51326044311185
 ],
 [
 -90.0,
 0.0
 ],
 [
 -180.0,
 0.0
 ],
 [
 -180.0,
 66.51326044311185
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -135.0,
 33.25663022155592,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 66.51326044311185,
 200000
 ],
 [
 -90.0,
 66.51326044311185,
 200000
 ],
 [
 -90.0,
 0.0,
 200000
 ],
 [
 -180.0,
 0.0,
 200000
 ],
 [
 -180.0,
 66.51326044311185,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 1,
 "zoom": 2
 },
 {
 "area_desc": "5.85e+07",
 "area_km2": 58475984.53846981,
 "bounds": [
 "-180.00",
 "-66.51",
 "-90.00",
 "0.00"
 ],
 "centroid_label": "(0,2)",
 "fill_color": [
 0,
 0,
 0
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 0.0
 ],
 [
 -90.0,
 0.0
 ],
 [
 -90.0,
 -66.51326044311185
 ],
 [
 -180.0,
 -66.51326044311185
 ],
 [
 -180.0,
 0.0
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -135.0,
 -33.25663022155592,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 0.0,
 200000
 ],
 [
 -90.0,
 0.0,
 200000
 ],
 [
 -90.0,
 -66.51326044311185,
 200000
 ],
 [
 -180.0,
 -66.51326044311185,
 200000
 ],
 [
 -180.0,
 0.0,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 2,
 "zoom": 2
 },
 {
 "area_desc": "5.04e+06",
 "area_km2": 5044532.457006394,
 "bounds": [
 "-180.00",
 "-85.05",
 "-90.00",
 "-66.51"
 ],
 "centroid_label": "(0,3)",
 "fill_color": [
 255,
 255,
 255
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 -66.51326044311185
 ],
 [
 -90.0,
 -66.51326044311185
 ],
 [
 -90.0,
 -85.05112877980659
 ],
 [
 -180.0,
 -85.05112877980659
 ],
 [
 -180.0,
 -66.51326044311185
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pyd

## Tiles - Zoom Level 3

For zoom level 3, the `x` and `y` tile indices range from 0 to 7[1].
There are a total of 64 tiles[2].

[1] $z=3; \ \ 2^z - 1 = 7$

[2] $z=3; \ \ 4^z = 64$ tiles

In [9]:
create_globe_with_xyz_tiles(3)

<iframe
 width="100%"
 height=500
 frameborder="0"
 srcdoc="<!DOCTYPE html>
<html>
 <head>
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 <title>pydeck</title>
 <script src="https://api.tiles.mapbox.com/mapbox-gl-js/v1.13.0/mapbox-gl.js"></script>
 <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css" />
 <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css" />
 <script src='https://cdn.jsdelivr.net/npm/@deck.gl/jupyter-widget@~8.8.*/dist/index.js'></script>
 <style>
 body {
 margin: 0;
 padding: 0;
 overflow: hidden;
}

#deck-container {
 width: 100vw;
 height: 100vh;
}

#deck-container canvas {
 z-index: 1;
 background: none;
}
 </style>
 </head>
 <body>
 <div id="deck-container">
 </div>
 </body>
 <script>
 const container = document.getElementById('deck-container');
 const jsonInput = {
 "initialViewState": {
 "latitude": 45,
 "longitude": -45,
 "minZoom": 0,
 "zoom": 0
 },
 "layers": [
 {
 "@@type": "GeoJsonLayer",
 "data": "https://d2ad6b4ur7yvpq.cloudfront.net/naturalearth-3.3.0/ne_50m_admin_0_scale_rank.geojson",
 "extruded": false,
 "filled": true,
 "getFillColor": [
 200,
 200,
 200
 ],
 "getLineColor": [
 255,
 255,
 255
 ],
 "id": "base-map",
 "opacity": 0.5,
 "stroked": false
 },
 [
 {
 "@@type": "SolidPolygonLayer",
 "data": [
 {
 "area_desc": "4.49e+05",
 "area_km2": 448816.18357550603,
 "bounds": [
 "-180.00",
 "79.17",
 "-135.00",
 "85.05"
 ],
 "centroid_label": "(0,0)",
 "fill_color": [
 0,
 0,
 0
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 85.05112877980659
 ],
 [
 -135.0,
 85.05112877980659
 ],
 [
 -135.0,
 79.17133464081945
 ],
 [
 -180.0,
 79.17133464081945
 ],
 [
 -180.0,
 85.05112877980659
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -157.5,
 82.11123171031302,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 85.05112877980659,
 200000
 ],
 [
 -135.0,
 85.05112877980659,
 200000
 ],
 [
 -135.0,
 79.17133464081945,
 200000
 ],
 [
 -180.0,
 79.17133464081945,
 200000
 ],
 [
 -180.0,
 85.05112877980659,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 0,
 "zoom": 3
 },
 {
 "area_desc": "2.07e+06",
 "area_km2": 2073450.0449276913,
 "bounds": [
 "-180.00",
 "66.51",
 "-135.00",
 "79.17"
 ],
 "centroid_label": "(0,1)",
 "fill_color": [
 255,
 255,
 255
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 79.17133464081945
 ],
 [
 -135.0,
 79.17133464081945
 ],
 [
 -135.0,
 66.51326044311185
 ],
 [
 -180.0,
 66.51326044311185
 ],
 [
 -180.0,
 79.17133464081945
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -157.49999999999997,
 72.84229754196565,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 79.17133464081945,
 200000
 ],
 [
 -135.0,
 79.17133464081945,
 200000
 ],
 [
 -135.0,
 66.51326044311185,
 200000
 ],
 [
 -180.0,
 66.51326044311185,
 200000
 ],
 [
 -180.0,
 79.17133464081945,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 1,
 "zoom": 3
 },
 {
 "area_desc": "8.33e+06",
 "area_km2": 8331862.4136825865,
 "bounds": [
 "-180.00",
 "40.98",
 "-135.00",
 "66.51"
 ],
 "centroid_label": "(0,2)",
 "fill_color": [
 0,
 0,
 0
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 66.51326044311185
 ],
 [
 -135.0,
 66.51326044311185
 ],
 [
 -135.0,
 40.979898069620134
 ],
 [
 -180.0,
 40.979898069620134
 ],
 [
 -180.0,
 66.51326044311185
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -157.5,
 53.74657925636599,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 66.51326044311185,
 200000
 ],
 [
 -135.0,
 66.51326044311185,
 200000
 ],
 [
 -135.0,
 40.979898069620134,
 200000
 ],
 [
 -180.0,
 40.979898069620134,
 200000
 ],
 [
 -180.0,
 66.51326044311185,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 2,
 "zoom": 3
 },
 {
 "area_desc": "2.09e+07",
 "area_km2": 20906129.85555232,
 "bounds": [
 "-180.00",
 "0.00",
 "-135.00",
 "40.98"
 ],
 "centroid_label": "(0,3)",
 "fill_color": [
 255,
 255,
 255
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 40.979898069620134
 ],
 [
 -13

## Tiles - Zoom Level 4

For zoom level 4, the `x` and `y` tile indices range from 0 to 15[1].
There are a total of 256 tiles[2].

[1] $z=4; \ \ 2^z - 1 = 15$

[2] $z=4; \ \ 4^z = 256$ tiles

In [10]:
create_globe_with_xyz_tiles(4)

<iframe
 width="100%"
 height=500
 frameborder="0"
 srcdoc="<!DOCTYPE html>
<html>
 <head>
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 <title>pydeck</title>
 <script src="https://api.tiles.mapbox.com/mapbox-gl-js/v1.13.0/mapbox-gl.js"></script>
 <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css" />
 <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css" />
 <script src='https://cdn.jsdelivr.net/npm/@deck.gl/jupyter-widget@~8.8.*/dist/index.js'></script>
 <style>
 body {
 margin: 0;
 padding: 0;
 overflow: hidden;
}

#deck-container {
 width: 100vw;
 height: 100vh;
}

#deck-container canvas {
 z-index: 1;
 background: none;
}
 </style>
 </head>
 <body>
 <div id="deck-container">
 </div>
 </body>
 <script>
 const container = document.getElementById('deck-container');
 const jsonInput = {
 "initialViewState": {
 "latitude": 45,
 "longitude": -45,
 "minZoom": 0,
 "zoom": 0
 },
 "layers": [
 {
 "@@type": "GeoJsonLayer",
 "data": "https://d2ad6b4ur7yvpq.cloudfront.net/naturalearth-3.3.0/ne_50m_admin_0_scale_rank.geojson",
 "extruded": false,
 "filled": true,
 "getFillColor": [
 200,
 200,
 200
 ],
 "getLineColor": [
 255,
 255,
 255
 ],
 "id": "base-map",
 "opacity": 0.5,
 "stroked": false
 },
 [
 {
 "@@type": "SolidPolygonLayer",
 "data": [
 {
 "area_desc": "7.06e+04",
 "area_km2": 70617.17144447393,
 "bounds": [
 "-180.00",
 "82.68",
 "-157.50",
 "85.05"
 ],
 "centroid_label": "(0,0)",
 "fill_color": [
 0,
 0,
 0
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 85.05112877980659
 ],
 [
 -157.5,
 85.05112877980659
 ],
 [
 -157.5,
 82.67628497834903
 ],
 [
 -180.0,
 82.67628497834903
 ],
 [
 -180.0,
 85.05112877980659
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -168.74999999999997,
 83.86370687907781,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 85.05112877980659,
 200000
 ],
 [
 -157.5,
 85.05112877980659,
 200000
 ],
 [
 -157.5,
 82.67628497834903,
 200000
 ],
 [
 -180.0,
 82.67628497834903,
 200000
 ],
 [
 -180.0,
 85.05112877980659,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 0,
 "zoom": 4
 },
 {
 "area_desc": "1.54e+05",
 "area_km2": 153790.92034327908,
 "bounds": [
 "-180.00",
 "79.17",
 "-157.50",
 "82.68"
 ],
 "centroid_label": "(0,1)",
 "fill_color": [
 255,
 255,
 255
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 82.67628497834903
 ],
 [
 -157.5,
 82.67628497834903
 ],
 [
 -157.5,
 79.17133464081945
 ],
 [
 -180.0,
 79.17133464081945
 ],
 [
 -180.0,
 82.67628497834903
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -168.75,
 80.92380980958424,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 82.67628497834903,
 200000
 ],
 [
 -157.5,
 82.67628497834903,
 200000
 ],
 [
 -157.5,
 79.17133464081945,
 200000
 ],
 [
 -180.0,
 79.17133464081945,
 200000
 ],
 [
 -180.0,
 82.67628497834903,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 1,
 "zoom": 4
 },
 {
 "area_desc": "3.32e+05",
 "area_km2": 332143.91676215845,
 "bounds": [
 "-180.00",
 "74.02",
 "-157.50",
 "79.17"
 ],
 "centroid_label": "(0,2)",
 "fill_color": [
 0,
 0,
 0
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 79.17133464081945
 ],
 [
 -157.5,
 79.17133464081945
 ],
 [
 -157.5,
 74.01954331150228
 ],
 [
 -180.0,
 74.01954331150228
 ],
 [
 -180.0,
 79.17133464081945
 ]
 ]
 ],
 "type": "Polygon"
 },
 "pydeck_centroid": [
 -168.75,
 76.59543897616086,
 800000
 ],
 "pydeck_polygon": [
 [
 -180.0,
 79.17133464081945,
 200000
 ],
 [
 -157.5,
 79.17133464081945,
 200000
 ],
 [
 -157.5,
 74.01954331150228,
 200000
 ],
 [
 -180.0,
 74.01954331150228,
 200000
 ],
 [
 -180.0,
 79.17133464081945,
 200000
 ]
 ],
 "x_index": 0,
 "y_index": 2,
 "zoom": 4
 },
 {
 "area_desc": "7.05e+05",
 "area_km2": 704581.105701687,
 "bounds": [
 "-180.00",
 "66.51",
 "-157.50",
 "74.02"
 ],
 "centroid_label": "(0,3)",
 "fill_color": [
 255,
 255,
 255
 ],
 "geometry": {
 "coordinates": [
 [
 [
 -180.0,
 74.01954331150228
 ],
 [
 -157.5,

The preceding globes for level 2 and higher show how web mercator tiles
can distort the appearent size of regions at different latitudes. Roll
your cursor over the tile numbers for a quantitative comparison.